In [1]:
from pathlib import Path

import altair as alt
import pandas as pd
from IPython.display import display, HTML

In [2]:
save_figures = False
data_path = '../../data/openzh-covid-19'
figures_path = '../../figures'

In [3]:
# Parameters
save_figures = True
data_path = "data/openzh-covid-19/"
figures_path = "figures/"


In [4]:
html_credits=HTML('''
<p style="font-size: smaller">Data Sources: 
  <a href="https://github.com/openZH/covid_19">OpenData Zuerich</a>,
  <a href="https://www.bfs.admin.ch">Federal Statistical Office</a>
<br>
Analysis:
  <a href="https://renkulab.io/projects/covid-19/covid-19-public-data">Covid-19 Public Data Collaboration Project</a>
</p>''')

## Read in the data

We have two datasets for Switzerland - the COVID-19 dataset from https://github.com/openZH/covid_19 and the population statistics by age and canton. We can read both of these in to dataframes:

In [5]:
# read in cantonal data and produce one dataframe
df_list = []

for f in Path(data_path).glob('COVID19_Fallzahlen_Kanton_*total.csv'):
    df_list.append(pd.read_csv(f))

df = pd.concat(df_list)

df['date'] = pd.to_datetime(df['date'], dayfirst=True)

In [6]:
# read in population data
df_pop = pd.read_excel(
    Path(data_path) / '../ch-population-statistics/ch-population-by-age-canton.xls', 
    header=1, 
    skipfooter=5
)
df_pop = df_pop.where(
    df_pop.Region.str.startswith('-')
).dropna().sort_values('Region').reset_index(drop=True)

# match the cantons in the two datasets
df_pop['abbreviation_canton_and_fl'] = ['AG', 'AI', 'AR', 'BL', 'BS', 'BE', 'FR', 'GE', 'GL', 'GR', 'JU', 'LU', 'NE', 'NW', 'OW', 'SH', 'SZ', 'SO', 'SG', 'TG', 'TI', 'UR', 'VS', 'VD', 'ZG', 'ZH']

pop_d = df_pop[['abbreviation_canton_and_fl', 'Total']].set_index('abbreviation_canton_and_fl').to_dict()


# calculate cases and deaths per 10k

for x in ['conf', 'deceased']:
    df[f'ncumul_{x}_100k'] = df.apply(
        lambda row: row[f'ncumul_{x}']/pop_d['Total'][row.abbreviation_canton_and_fl]*100000, axis=1
    )

In [7]:
# display the dataframe
df.head()

date time abbreviation_canton_and_fl  ncumul_tested  ncumul_conf  \
0 2020-02-28  NaN                         VS            NaN          1.0   
1 2020-02-29  NaN                         VS            NaN          1.0   
2 2020-03-01  NaN                         VS            NaN          2.0   
3 2020-03-02  NaN                         VS            NaN          3.0   
4 2020-03-03  NaN                         VS            NaN          3.0   

   ncumul_hosp  ncumul_ICU  ncumul_vent  ncumul_released  ncumul_deceased  \
0          3.0         NaN          NaN              NaN              NaN   
1          3.0         NaN          NaN              NaN              NaN   
2          4.0         NaN          NaN              NaN              NaN   
3          4.0         NaN          NaN              NaN              NaN   
4          5.0         NaN          NaN              NaN              NaN   

                                              source  ncumul_ICF  \
0  https://vs.ch/documents/529400/6767345/2020+02...         NaN   
1  https://www.vs.ch/documents/6756452/7008787/Si...         NaN   
2  https://www.vs.ch/documents/6756452/7008787/Si...         NaN   
3  https://www.vs.ch/documents/6756452/7008787/Si...         NaN   
4  https://vs.ch/documents/529400/6789273/2020+03...         NaN   

   ncumul_ICU_intub  ncumul_deceased_suspect  TotalPosTests1  TotalCured  \
0               NaN                      NaN             NaN         NaN   
1               NaN                      NaN             NaN         NaN   
2               NaN                      NaN             NaN         NaN   
3               NaN                      NaN             NaN         NaN   
4               NaN                      NaN             NaN         NaN   

   ncumul_conf_100k  ncumul_deceased_100k  
0          0.290736                   NaN  
1          0.290736                   NaN  
2          0.581471                   NaN  
3          0.872207                   NaN  
4          0.872207                   NaN

## Plot the available data

Below we make plots of total cases, total cases per 10k population and total deaths. You can click on the canton abbreviations in the legend to highlight individual lines. 

In [8]:
def generate_canton_chart(column, title, tooltip_title):
    """Produce a canton chart given a column name"""
    selection = alt.selection_multi(fields=['abbreviation_canton_and_fl'], bind='legend')
    chart = base.mark_line().encode(
        alt.X('date', title='Date'), 
        alt.Y(column, 
              title=title, scale=alt.Scale(type='linear')),
        color=alt.Color('abbreviation_canton_and_fl', legend=alt.Legend(title="Canton")),
        tooltip=[alt.Tooltip('abbreviation_canton_and_fl',title='Canton'),
                 alt.Tooltip(column,title=tooltip_title),
                 alt.Tooltip('date',title='Date')],
        opacity=alt.condition(selection, alt.value(1), alt.value(0.2))
    ).add_selection(
        selection
    )
    return chart

### Total cases

In [9]:
base = alt.Chart(df.where(df.ncumul_conf>0).dropna(subset=['abbreviation_canton_and_fl']))
base.configure_header(titleFontSize=25)
base.configure_axis(labelFontSize=15, titleFontSize=15)

cumul = generate_canton_chart('ncumul_conf', 'Cases', 'Cases')
cumul_100k = generate_canton_chart('ncumul_conf_100k', 'Cases per 100k population', 'Cases/100k')

chart = alt.hconcat(
    cumul, cumul_100k, title='Covid-19 cases in Switzerland by Canton'
).configure_title(
    anchor='middle'
)

display(chart)
if save_figures:
    chart.save(str(Path(figures_path) / 'switzerland-cases-by-canton.html'))
    
display(html_credits)

alt.HConcatChart(...)

### Deaths

In [10]:
base = alt.Chart(df.where(df.ncumul_deceased>0).dropna(subset=['abbreviation_canton_and_fl']))
base.configure_header(titleFontSize=25)
base.configure_axis(labelFontSize=15, titleFontSize=15)

deaths = generate_canton_chart('ncumul_deceased', 'Deaths', 'Deaths')
deaths_100k = generate_canton_chart('ncumul_deceased_100k', 'Deaths per 100k population', 'Deaths/100k')

chart = alt.hconcat(
    deaths, deaths_100k, title='Covid-19 deaths in Switzerland by Canton'
).configure_title(
    anchor='middle'
)
display(chart)    
display(html_credits)

if save_figures:
    chart.save(str(Path(figures_path) / 'switzerland-deaths-by-canton.html'))


alt.HConcatChart(...)